In [22]:
import pandas as pd
import seaborn as sns
import numpy as np

from scipy import stats

import plotly.express as px
import plotly.graph_objects as go

In [2]:
quant_df = pd.read_csv("../../data/processed/lc-ms_sc_1_iimn_gnps_quant.csv")
quantifications_df = quant_df[[col for col in quant_df.columns if "Peak area" in col]]

In [62]:
fig = go.Figure(
                data=go.Heatmap(x=quantifications_df.columns,
                                y=quantifications_df.index,
                                z=quantifications_df,
                                colorscale="Inferno"),
                layout={"height": 800})
fig.show()

## Accumulation in strains

In [4]:
quantifications_xblank = quantifications_df[[col for col in quantifications_df.columns if "blank" not in col.lower()]]

In [52]:
summed_signals = pd.DataFrame({"Signals found": np.sum(quantifications_xblank > 0.0, axis=0)})
fig = px.histogram(summed_signals, x="Signals found", nbins=20)
fig.update_layout( yaxis_title="Number of strains (#)" )
fig.show()

In [53]:
summed_signals = pd.DataFrame({"Signal intensity": quantifications_xblank.sum()})
fig = px.histogram(summed_signals, x="Signal intensity", nbins=20)
fig.update_layout( yaxis_title="Number of strains (#)" )
fig.show()

## Scoring

In [7]:
zscores = stats.zscore(quantifications_df, axis=1)

In [67]:
fig = go.Figure(data=go.Heatmap(x=quantifications_df.columns,
                                y=quantifications_df.index,
                                z=zscores,
                                zmin=-15.0,
                                zmax=15,
                                colorscale="Tropic"),
                layout={"height": 800})
fig.show()

In [12]:
def plot_cutoff_accumulation(zscores:pd.DataFrame, cutoff_range:tuple, axis:int=0, sample_marker=None):
    score_cutoffs = pd.DataFrame({i: np.sum((zscores > i) | (zscores < -i), axis=axis) for i in range(*cutoff_range)})
    names = score_cutoffs.index
    if sample_marker:
        marked_samples = [sample_marker in name for name in names] 
        score_cutoffs[sample_marker] = marked_samples
        fig = px.strip(score_cutoffs, color=sample_marker, hover_name=names)
    else:
        fig = px.strip(score_cutoffs, hover_name=names)
    fig.update_layout( xaxis_title="z-score cutoff", yaxis_title="Strains per metabolites" if axis else "Metabolites per strain",
                       hovermode="x", )
    #fig.data[0].update(span = (0, None), spanmode='manual')
    fig.show()

In [13]:
plot_cutoff_accumulation(zscores=zscores, cutoff_range=(3,10), axis=1)

In [14]:
plot_cutoff_accumulation(zscores=zscores, cutoff_range=(4,10), axis=0, sample_marker="blank")

## Merge annotations

In [15]:
structures_df = pd.read_csv("../../project_batches/sirius/summaries/structure_identifications.tsv", sep="\t")

In [16]:
annot_df = pd.concat([quant_df["row ID"], zscores], axis=1, )

In [17]:
def read_filter_sirius(file_path, filter_column, threshold_value:float) -> pd.DataFrame:
    df = pd.read_csv( file_path, sep="\t")
    df.replace("-Infinity", -np.inf, inplace=True)
    df[filter_column] = df[filter_column].replace(",", ".", regex=True).astype(float)
    solid_df = df.loc[df[filter_column] >= threshold_value]
    return solid_df.sort_values(filter_column, ascending=False)

In [18]:
solid_sirius_formulas = read_filter_sirius("../../project_batches/sirius/summaries/formula_identifications.tsv", "ZodiacScore", 0.5)
solid_sirius_formulas

formulaRank molecularFormula          adduct precursorFormula  \
318            1         C17H22O2  [M + H3N + H]+       C17H26NO2+   
0              1         C7H10N2O  [M + H3N + H]+        C7H14N3O+   
294            1           C8H8O4  [M + H3N + H]+        C8H12NO4+   
292            1     C2H4ClFN2O2S        [M - H]-    C2H3ClFN2O2S-   
289            1           C5H6O4  [M + H3N + H]+        C5H10NO4+   
..           ...              ...             ...              ...   
12             1      C32H62N4O10  [M + H3N + H]+     C32H66N5O10+   
107            1            H2O3P       [M + Na]+         H2NaO3P+   
256            1           C4H6O3        [M - H]-          C4H5O3-   
15             1         C40H60O7  [M + H3N + H]+       C40H64NO7+   
188            1         C5H7BFN3  [M + H3N + H]+       C5H11BFN4+   

     ZodiacScore SiriusScore TreeScore IsotopeScore  numExplainedPeaks  \
318        1.000     141,567   138,148        3,419                 37   
0          1.000      65,864    65,864        0,000                 26   
294        1.000     172,340   170,074        2,267                 28   
292        1.000      48,196    48,196        0,000                 11   
289        1.000      72,754    72,754        0,000                 17   
..           ...         ...       ...          ...                ...   
12         0.517      72,103    64,722        7,381                 34   
107        0.512      -5,215    -5,215        0,000                  0   
256        0.506       4,500     4,500        0,000                  0   
15         0.505      85,401    76,112        9,289                 34   
188        0.504      37,665    37,665        0,000                 12   

    explainedIntensity  ... medianAbsoluteMassErrorFragmentPeaks(ppm)  \
318              0,599  ...                                     4,439   
0                0,829  ...                                     9,135   
294              0,676  ...                                     6,862   
292              0,494  ...                                     5,650   
289              0,762  ...                                     6,378   
..                 ...  ...                                       ...   
12               0,823  ...                                     2,958   
107              0,000  ...                                       NaN   
256              0,000  ...                                       NaN   
15               0,793  ...                                     6,171   
188              0,650  ...                                    12,800   

    massErrorPrecursor(ppm) lipidClass  ionMass retentionTimeInSeconds  \
318                  -0,471        NaN  276,196                    120   
0                   -17,386        NaN  156,110                      3   
294                  -0,003        NaN  186,076                     88   
292                   0,649        NaN  172,959                     85   
289                   0,076        NaN  148,060                     83   
..                      ...        ...      ...                    ...   
12                   -0,639        NaN  680,480                     14   
107                  -9,198        NaN  103,962                     28   
256                   8,339        NaN  101,025                     75   
15                   -0,266        NaN  670,468                     14   
188                  11,607        NaN  156,111                     41   

     retentionTimeInMinutes           formulaId    alignedFeatureId  \
318                   1,992  633592464038598105  633591814802215644   
0                     0,045  633592390407567197  633591789191793566   
294                   1,461  633592390399178521  633591813489398313   
292                   1,421  633592390281737826  633591814399562390   
289                   1,381  633592363530458132  633591813975937631   
..                      ...                 ...                 ...   
12          

In [19]:
solid_sirius_structures = read_filter_sirius("../../project_batches/sirius/summaries/structure_identifications.tsv", "ConfidenceScoreApproximate", 0.5)
solid_sirius_structures

structurePerIdRank  formulaRank ConfidenceScoreExact  \
141                   1            1                0,990   
196                   1            1                0,936   
96                    1            1                0,878   
225                   1            1                0,930   
230                   1            1                0,722   
146                   1            1                0,873   
200                   1            1                0,863   
236                   1            2                0,387   
94                    1            1                0,813   
187                   1            2                0,807   
104                   1            1                0,806   
194                   1            1                0,805   
235                   1            2                0,696   
232                   1            1                0,760   
15                    1            1                0,673   
14                    1            1                0,664   
130                   1            1                0,533   
28                    1            1                0,566   
253                   1            1                0,639   
210                   1            1                0,501   
124                   1            1                0,619   
82                    1            1                0,597   
62                    1            1                0,545   
31                    1            3                0,556   
63                    1            1                0,221   
182                   1            2                0,545   
123                   1            1                0,234   
116                   1            1                0,192   
138                   1            1                0,538   
121                   1            1                0,174   
134                   1            1                0,177   
112                   1            1                0,172   

     ConfidenceScoreApproximate CSI:FingerIDScore ZodiacScore SiriusScore  \
141                       0.990            -6,895       1,000      60,344   
196                       0.986            -7,672       1,000      53,832   
96                        0.976           -15,395       1,000      76,945   
225                       0.968            -8,759       0,946     103,022   
230                       0.879           -37,394       1,000     164,031   
146                       0.873           -27,361       0,693      38,514   
200                       0.863           -15,052       0,986      56,451   
236                       0.857            -4,535       0,012      42,148   
94                        0.813          -425,904       1,000      50,474   
187                       0.807           -25,826       0,015      94,566   
104                       0.806          -431,452       1,000      45,761   
194                       0.805           -86,598       0,957     115,471   
235                       0.793           -32,360       0,406      22,818   
232                       0.760           -11,001       1,000      54,355   
15                        0.673          -139,373       0,998     104,686   
14                        0.664          -147,028       0,980     117,244   
130                       0.654          -160,055       1,000    7140,076   
28                        0.650            -4,237       1,000    7030,431   
253                       0.639          -143,014       0,994      66,995   
210                       0.636           -41,874       1,000     138,965   
124                       0.619          -222,675       1,000    4065,386   
82                        0.597           -99,796       0,000      65,817   
62                        0.586          -213,932       1,000    8123,417   
31                        0.556           -30,479       0,235      46,697   
63                        0.546          -222,224       1,000    6

In [20]:
solid_sirius_denovo_structures = read_filter_sirius("../../project_batches/sirius/summaries/denovo_structure_identifications.tsv", "CSI:FingerIDScore", -1000)
solid_sirius_denovo_structures

# INCLUDE DE NOVO IF CSI:FingerIDScore De Novo < CSI:FingerIDScore Structures

structurePerIdRank  formulaRank  CSI:FingerIDScore ModelScore  \
60                    1            1             -3.739     -1,913   
25                    1            3             -4.027     -0,153   
32                    1            1             -4.237     -0,742   
245                   1            2             -4.535     -0,155   
100                   1            1             -5.267     -4,414   
..                  ...          ...                ...        ...   
52                    1            2           -370.673    -14,659   
38                    1            1           -428.159    -14,779   
77                    1            1           -479.432    -11,898   
17                    1            1           -485.463    -13,697   
88                    1            1           -548.966    -13,974   

    ZodiacScore SiriusScore molecularFormula          adduct precursorFormula  \
60        1,000     125,130       C37H72NO8P        [M - H]-      C37H71NO8P-   
25        0,027      13,888         C4HF9O3S        [M - H]-         C4F9O3S-   
32        1,000    7030,431       C42H79O10P        [M - H]-      C42H78O10P-   
245       0,012      42,148           C4H6O5        [M - H]-          C4H5O5-   
100       1,000      74,517       C39H74NO8P        [M - H]-      C39H73NO8P-   
..          ...         ...              ...             ...              ...   
52        0,034      84,105       C39H59NO13        [M + H]+      C39H60NO13+   
38        1,000      63,299       C43H67N3O6        [M - H]-      C43H66N3O6-   
77        0,000      41,198       C26H36N2O6        [M + H]+      C26H37N2O6+   
17        0,994     148,905       C25H32N2O8        [M + H]+      C25H33N2O8+   
88        0,969      61,757       C40H52N4O9  [M + H3N + H]+      C40H56N5O9+   

         InChIkey2D                                              InChI  \
60   CZOSTDZGCCEZTJ  InChI=1S/C37H72NO8P/c1-3-5-7-9-11-13-15-17-19-...   
25   JGTNAGYHADQMCM  InChI=1S/C4HF9O3S/c5-1(6,3(9,10)11)2(7,8)4(12,...   
32   DSNRWDQKZIEDDB  InChI=1S/C42H79O10P/c1-3-5-7-9-11-13-15-17-19-...   
245  BJEPYKJPYRNKOW  InChI=1S/C4H6O5/c5-2(4(8)9)1-3(6)7/h2,5H,1H2,(...   
100  UIELPOKGTOHFNL  InChI=1S/C39H74NO8P/c1-3-5-7-9-11-13-15-17-18-...   
..              ...                                                ...   
52   FASQQSYDIVROID  InChI=1S/C39H59NO13/c1-17-10-27(51-36(49)24(17...   
38   BWWQFRYTRDMDLG  InChI=1S/C43H67N3O6/c1-4-6-8-10-12-14-15-16-17...   
77   HTUDYBHLJVZOOG  InChI=1S/C26H36N2O6/c1-18(2)9-8-11-20(4)15-19(...   
17   BWNNXKLVEMGRJO  InChI=1S/C25H32N2O8/c1-13(2)11-16(28)20-18(24(...   
88   OYCFMZCQQUXGDR  InChI=1S/C40H52N4O9/c1-27(2)18-14-11-9-7-8-10-...   

                                                  name  \
60   (2-aminoethoxy)[2-(hexadec-9-enoyloxy)-3-(hexa...   
25                                                 NaN   
32   1,2-Di-(9E-Octadecenoyl)-Sn-Glycero-3-Phospho-...   
245                                             Malate   
100  (2-aminoethoxy)[2-(hexadec-9-enoyloxy)-3-(octa...   
..                                                 ...   
52                                                 NaN   
38                                                 NaN   
77                                                 NaN   
17                                                 NaN   
88                                                 NaN   

                                                smiles  ionMass  \
60   CCCCCCCCCCCCCCCC(=O)OCC(COP(=O)(O)OCCN)OC(=O)C...  688,496   
25           C(C(C(F)(F)S(=O)(=O)O)(F)F)(C(F)(F)F)(F)F  298,945   
32   CCCCCCCCC=CCCCCCCCC(=O)OCC(COP(=O)(O)OCC(CO)O)...  773,538   
245                                C(C(C(=O)O)O)C(=O)O  133,015   
100  CCCCCCCCC=CCCCCCCCC(=O)OCC(COP(=O)(O)OCCN)OC(=...  714,512   
..                                                 ...      ...   
52   CC1=C(COC2OC(CO)C(O)C(O)C2O)C(=O)OC(C(C)C(O)C(...  750,407   
38   CCCCCCCCCCCCCCCC(=O)NC1C(=O)C(OC(=O)C2=Nc3cccc...  720,495   
77

In [21]:
solid_sirius_denovo_structures = read_filter_sirius("../../project_batches/sirius/summaries/canopus_structure_summary.tsv", "CSI:FingerIDScore", -1000)
solid_sirius_denovo_structures

# Strctures:
"""
NPC#pathway	NPC#pathway Probability	NPC#superclass	NPC#superclass Probability	NPC#class	NPC#class Probability
ClassyFire#superclass	ClassyFire#superclass probability	ClassyFire#class	ClassyFire#class Probability	ClassyFire#subclass	ClassyFire#subclass Probability
ClassyFire#level 5	ClassyFire#level 5 Probability	ClassyFire#most specific class	ClassyFire#most specific class Probability	ClassyFire#all classifications	
ionMass	retentionTimeInSeconds	retentionTimeInMinutes	formulaId	alignedFeatureId	mappingFeatureId	overallFeatureQuality
"""
# 

KeyError: 'CSI:FingerIDScore'